In [1]:
import os
import pandas as pd
from PIL import Image
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader, random_split
from torchvision import transforms, models

# ======================================================
# Device Setup: Use MPS if available (M1 Pro), CUDA if available, else CPU.
# ======================================================
if torch.backends.mps.is_available():
    device = torch.device("mps")
elif torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")
print(f"[Device Setup] Using device: {device}\n")

# ======================================================
# 1. Set Up Paths and Load CSV
# ======================================================
base_dir = '/Users/bhaskarpramodchennupalli/Documents/Image_Detector'
csv_path = os.path.join(base_dir, 'train.csv')
train_data_dir = os.path.join(base_dir, 'train_data')

print("=== Step 1: Data Check and CSV Load ===")
df = pd.read_csv(csv_path)
if 'Unnamed: 0' in df.columns:
    df = df.drop(columns=['Unnamed: 0'])
print(f"[Step 1] Loaded CSV file with {len(df)} records.")

# Optional: Check that every file exists in the train_data directory.
missing_files = []
for i, file_path in enumerate(df['file_name']):
    filename = os.path.basename(file_path)
    full_path = os.path.join(train_data_dir, filename)
    if not os.path.exists(full_path):
        missing_files.append(full_path)
    if i % 100 == 0:
        print(f"[Step 1] Checked {i} files...")
if missing_files:
    print(f"[Step 1] Missing {len(missing_files)} files:")
    for f in missing_files:
        print("    Missing:", f)
else:
    print("[Step 1] All files exist in the train_data directory!")
print("[Step 1] Data check complete.\n")

# ======================================================
# 2. Define the Custom Dataset Class (Top-Level)
# ======================================================
print("=== Step 2: Define Custom Dataset Class ===")
class CustomImageDataset(Dataset):
    def __init__(self, csv_file, transform=None):
        print(f"[Dataset Init] Loading CSV file: {csv_file}")
        self.data_frame = pd.read_csv(csv_file)
        if 'Unnamed: 0' in self.data_frame.columns:
            self.data_frame = self.data_frame.drop(columns=['Unnamed: 0'])
        self.transform = transform
        print(f"[Dataset Init] Loaded {len(self.data_frame)} records from {csv_file}")

    def __len__(self):
        return len(self.data_frame)

    def __getitem__(self, idx):
        file_path = self.data_frame.iloc[idx]['file_name']
        filename = os.path.basename(file_path)
        full_path = os.path.join(train_data_dir, filename)
        try:
            image = Image.open(full_path).convert("RGB")
        except Exception as e: # Catching more general exceptions during image loading
            print(f"[Dataset __getitem__] Error loading image: {full_path}, error: {e}")
            image = Image.new("RGB", (224, 224), "white") # Return a white image if loading fails

        if self.transform:
            image = self.transform(image)
        label = self.data_frame.iloc[idx]['label']
        return image, label

print("[Step 2] CustomImageDataset class defined.\n")

# ======================================================
# 3. Define ResNet50 (Top-Level) - UPDATED to ResNet50
# ======================================================
print("=== Step 3: Define Candidate Model Architecture (ResNet50) ===")

# Candidate: Pretrained ResNet50 fine-tuned for binary classification - UPDATED
def create_resnet50():
    weights = models.ResNet50_Weights.DEFAULT # UPDATED to ResNet50 weights
    model = models.resnet50(weights=weights) # UPDATED to resnet50
    num_ftrs = model.fc.in_features
    model.fc = nn.Linear(num_ftrs, 1)
    return model

print("[Step 3] ResNet50 model defined.\n") # UPDATED message

# Store ResNet50 model in dictionary - UPDATED key to ResNet50
candidates = {
    "ResNet50": create_resnet50() # UPDATED to use create_resnet50
}
print("[Step 3] Candidate model (ResNet50) stored in dictionary.\n") # UPDATED message

# ======================================================
# 4. Define Transformations & Create Dataset, Split, and DataLoaders (Top-Level)
# ======================================================
print("=== Step 4: Create Dataset, Split, and DataLoaders ===")
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    # Uncomment if normalization is required:
    # transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])
print("[Step 4] Image transformations defined.")

print("[Step 4] Creating full dataset...")
full_dataset = CustomImageDataset(csv_file=csv_path, transform=transform)
print(f"[Step 4] Full dataset size: {len(full_dataset)}")

# Split dataset into training and validation (80/20 split)
train_size = int(0.8 * len(full_dataset))
val_size = len(full_dataset) - train_size
train_dataset, val_dataset = random_split(full_dataset, [train_size, val_size])
print(f"[Step 4] Training set size: {len(train_dataset)}")
print(f"[Step 4] Validation set size: {len(val_dataset)}")

batch_size = 32
print(f"[Step 4] Creating DataLoaders with batch size {batch_size} and num_workers=0 (for Jupyter)...")
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=0)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False, num_workers=0)
print("[Step 4] DataLoaders created.\n")

# ======================================================
# 5. Define Training and Evaluation Functions (Top-Level)
# ======================================================
print("=== Step 5: Define Training and Evaluation Functions ===")
def train_and_evaluate(model, train_loader, val_loader, criterion, optimizer, num_epochs, device):
    model.to(device)
    best_val_acc = 0.0
    print("[Train & Eval] Starting training loop...") # ADDED: Start of train_and_evaluate
    for epoch in range(num_epochs):
        print(f"[Train & Eval] Epoch {epoch+1}/{num_epochs} starting...") # ADDED: Epoch start
        model.train()
        running_loss = 0.0
        print("[Train & Eval] Entering train_loader loop...") # ADDED: Before train_loader loop
        for batch_idx, (images, labels) in enumerate(train_loader): # ADDED batch_idx for debugging
            print(f"[Train & Eval] Batch {batch_idx} - Data loading...") # ADDED: Batch start
            images = images.to(device)
            labels = labels.float().unsqueeze(1).to(device)
            print(f"[Train & Eval] Batch {batch_idx} - Data moved to device.") # ADDED: Data to device
            optimizer.zero_grad()
            print(f"[Train & Eval] Batch {batch_idx} - Gradients zeroed.") # ADDED: Gradients zeroed
            outputs = model(images)
            print(f"[Train & Eval] Batch {batch_idx} - Forward pass complete.") # ADDED: Forward pass
            loss = criterion(outputs, labels)
            print(f"[Train & Eval] Batch {batch_idx} - Loss calculated.") # ADDED: Loss calc
            loss.backward()
            print(f"[Train & Eval] Batch {batch_idx} - Backward pass complete.") # ADDED: Backward pass
            optimizer.step()
            print(f"[Train & Eval] Batch {batch_idx} - Optimizer step complete.") # ADDED: Optimizer step
            running_loss += loss.item() * images.size(0)
        avg_loss = running_loss / len(train_loader.dataset)
        print(f"[Train & Eval] Epoch {epoch+1}/{num_epochs} - Training Loss calculated.") # ADDED: Epoch train loss

        # Evaluate on validation set
        model.eval()
        correct = 0
        total = 0
        print("[Train & Eval] Entering val_loader loop...") # ADDED: Before val_loader loop
        with torch.no_grad():
            for val_batch_idx, (images, labels) in enumerate(val_loader): # ADDED val_batch_idx
                print(f"[Train & Eval] Val Batch {val_batch_idx} - Data loading...") # ADDED: Val Batch start
                images = images.to(device)
                labels = labels.float().unsqueeze(1).to(device)
                outputs = model(images)
                preds = torch.round(torch.sigmoid(outputs))
                total += labels.size(0)
                correct += (preds == labels).sum().item()
        val_acc = correct / total
        print(f"[Step 5] Epoch {epoch+1}/{num_epochs} | Train Loss: {avg_loss:.4f} | Val Acc: {val_acc*100:.2f}%")
        best_val_acc = max(best_val_acc, val_acc)
    return best_val_acc

criterion = nn.BCEWithLogitsLoss()
print("[Step 5] Training and evaluation functions defined.\n")

# ======================================================
# 6. Train ResNet50 Model - UPDATED to train ResNet50
# ======================================================
print("=== Step 6: Training ResNet50 Model ===") # UPDATED message
num_epochs = 5
results = {}
for name, model_candidate in candidates.items(): # This will now iterate over ResNet50
    print(f"\n[Step 6] Training model: {name}")
    model_candidate.to(device)
    optimizer = optim.Adam(model_candidate.parameters(), lr=0.001)
    val_acc = train_and_evaluate(model_candidate, train_loader, val_loader, criterion, optimizer, num_epochs, device)
    results[name] = val_acc
    print(f"[Step 6] Model {name} achieved validation accuracy: {val_acc*100:.2f}%")

print("\n=== Step 6: Model Selection Results ===")
for name, acc in results.items():
    print(f"{name}: {acc*100:.2f}% validation accuracy")
best_model_name = max(results, key=results.get)
print(f"\n[Step 6] Best model: {best_model_name} with {results[best_model_name]*100:.2f}% validation accuracy")
print("=== Training Complete ===\n")

[Device Setup] Using device: mps

=== Step 1: Data Check and CSV Load ===
[Step 1] Loaded CSV file with 91950 records.
[Step 1] Checked 0 files...
[Step 1] Checked 100 files...
[Step 1] Checked 200 files...
[Step 1] Checked 300 files...
[Step 1] Checked 400 files...
[Step 1] Checked 500 files...
[Step 1] Checked 600 files...
[Step 1] Checked 700 files...
[Step 1] Checked 800 files...
[Step 1] Checked 900 files...
[Step 1] Checked 1000 files...
[Step 1] Checked 1100 files...
[Step 1] Checked 1200 files...
[Step 1] Checked 1300 files...
[Step 1] Checked 1400 files...
[Step 1] Checked 1500 files...
[Step 1] Checked 1600 files...
[Step 1] Checked 1700 files...
[Step 1] Checked 1800 files...
[Step 1] Checked 1900 files...
[Step 1] Checked 2000 files...
[Step 1] Checked 2100 files...
[Step 1] Checked 2200 files...
[Step 1] Checked 2300 files...
[Step 1] Checked 2400 files...
[Step 1] Checked 2500 files...
[Step 1] Checked 2600 files...
[Step 1] Checked 2700 files...
[Step 1] Checked 2800 fil

[Step 1] Checked 36300 files...
[Step 1] Checked 36400 files...
[Step 1] Checked 36500 files...
[Step 1] Checked 36600 files...
[Step 1] Checked 36700 files...
[Step 1] Checked 36800 files...
[Step 1] Checked 36900 files...
[Step 1] Checked 37000 files...
[Step 1] Checked 37100 files...
[Step 1] Checked 37200 files...
[Step 1] Checked 37300 files...
[Step 1] Checked 37400 files...
[Step 1] Checked 37500 files...
[Step 1] Checked 37600 files...
[Step 1] Checked 37700 files...
[Step 1] Checked 37800 files...
[Step 1] Checked 37900 files...
[Step 1] Checked 38000 files...
[Step 1] Checked 38100 files...
[Step 1] Checked 38200 files...
[Step 1] Checked 38300 files...
[Step 1] Checked 38400 files...
[Step 1] Checked 38500 files...
[Step 1] Checked 38600 files...
[Step 1] Checked 38700 files...
[Step 1] Checked 38800 files...
[Step 1] Checked 38900 files...
[Step 1] Checked 39000 files...
[Step 1] Checked 39100 files...
[Step 1] Checked 39200 files...
[Step 1] Checked 39300 files...
[Step 1]

[Step 1] Checked 73800 files...
[Step 1] Checked 73900 files...
[Step 1] Checked 74000 files...
[Step 1] Checked 74100 files...
[Step 1] Checked 74200 files...
[Step 1] Checked 74300 files...
[Step 1] Checked 74400 files...
[Step 1] Checked 74500 files...
[Step 1] Checked 74600 files...
[Step 1] Checked 74700 files...
[Step 1] Checked 74800 files...
[Step 1] Checked 74900 files...
[Step 1] Checked 75000 files...
[Step 1] Checked 75100 files...
[Step 1] Checked 75200 files...
[Step 1] Checked 75300 files...
[Step 1] Checked 75400 files...
[Step 1] Checked 75500 files...
[Step 1] Checked 75600 files...
[Step 1] Checked 75700 files...
[Step 1] Checked 75800 files...
[Step 1] Checked 75900 files...
[Step 1] Checked 76000 files...
[Step 1] Checked 76100 files...
[Step 1] Checked 76200 files...
[Step 1] Checked 76300 files...
[Step 1] Checked 76400 files...
[Step 1] Checked 76500 files...
[Step 1] Checked 76600 files...
[Step 1] Checked 76700 files...
[Step 1] Checked 76800 files...
[Step 1]

[Train & Eval] Batch 3 - Optimizer step complete.
[Train & Eval] Batch 4 - Data loading...
[Train & Eval] Batch 4 - Data moved to device.
[Train & Eval] Batch 4 - Gradients zeroed.
[Train & Eval] Batch 4 - Forward pass complete.
[Train & Eval] Batch 4 - Loss calculated.
[Train & Eval] Batch 4 - Backward pass complete.
[Train & Eval] Batch 4 - Optimizer step complete.
[Train & Eval] Batch 5 - Data loading...
[Train & Eval] Batch 5 - Data moved to device.
[Train & Eval] Batch 5 - Gradients zeroed.
[Train & Eval] Batch 5 - Forward pass complete.
[Train & Eval] Batch 5 - Loss calculated.
[Train & Eval] Batch 5 - Backward pass complete.
[Train & Eval] Batch 5 - Optimizer step complete.
[Train & Eval] Batch 6 - Data loading...
[Train & Eval] Batch 6 - Data moved to device.
[Train & Eval] Batch 6 - Gradients zeroed.
[Train & Eval] Batch 6 - Forward pass complete.
[Train & Eval] Batch 6 - Loss calculated.
[Train & Eval] Batch 6 - Backward pass complete.
[Train & Eval] Batch 6 - Optimizer step 

[Train & Eval] Batch 29 - Backward pass complete.
[Train & Eval] Batch 29 - Optimizer step complete.
[Train & Eval] Batch 30 - Data loading...
[Train & Eval] Batch 30 - Data moved to device.
[Train & Eval] Batch 30 - Gradients zeroed.
[Train & Eval] Batch 30 - Forward pass complete.
[Train & Eval] Batch 30 - Loss calculated.
[Train & Eval] Batch 30 - Backward pass complete.
[Train & Eval] Batch 30 - Optimizer step complete.
[Train & Eval] Batch 31 - Data loading...
[Train & Eval] Batch 31 - Data moved to device.
[Train & Eval] Batch 31 - Gradients zeroed.
[Train & Eval] Batch 31 - Forward pass complete.
[Train & Eval] Batch 31 - Loss calculated.
[Train & Eval] Batch 31 - Backward pass complete.
[Train & Eval] Batch 31 - Optimizer step complete.
[Train & Eval] Batch 32 - Data loading...
[Train & Eval] Batch 32 - Data moved to device.
[Train & Eval] Batch 32 - Gradients zeroed.
[Train & Eval] Batch 32 - Forward pass complete.
[Train & Eval] Batch 32 - Loss calculated.
[Train & Eval] Batc

...

[Train & Eval] Batch 2280 - Optimizer step complete.
[Train & Eval] Batch 2281 - Data loading...
[Train & Eval] Batch 2281 - Data moved to device.
[Train & Eval] Batch 2281 - Gradients zeroed.
[Train & Eval] Batch 2281 - Forward pass complete.
[Train & Eval] Batch 2281 - Loss calculated.
[Train & Eval] Batch 2281 - Backward pass complete.
[Train & Eval] Batch 2281 - Optimizer step complete.
[Train & Eval] Batch 2282 - Data loading...
[Train & Eval] Batch 2282 - Data moved to device.
[Train & Eval] Batch 2282 - Gradients zeroed.
[Train & Eval] Batch 2282 - Forward pass complete.
[Train & Eval] Batch 2282 - Loss calculated.
[Train & Eval] Batch 2282 - Backward pass complete.
[Train & Eval] Batch 2282 - Optimizer step complete.
[Train & Eval] Batch 2283 - Data loading...
[Train & Eval] Batch 2283 - Data moved to device.
[Train & Eval] Batch 2283 - Gradients zeroed.
[Train & Eval] Batch 2283 - Forward pass complete.
[Train & Eval] Batch 2283 - Loss calculated.
[Train & Eval] Batch 2283 - B

[Train & Eval] Val Batch 42 - Data loading...
[Train & Eval] Val Batch 43 - Data loading...
[Train & Eval] Val Batch 44 - Data loading...
[Train & Eval] Val Batch 45 - Data loading...
[Train & Eval] Val Batch 46 - Data loading...
[Train & Eval] Val Batch 47 - Data loading...
[Train & Eval] Val Batch 48 - Data loading...
[Train & Eval] Val Batch 49 - Data loading...
[Train & Eval] Val Batch 50 - Data loading...
[Train & Eval] Val Batch 51 - Data loading...
[Train & Eval] Val Batch 52 - Data loading...
[Train & Eval] Val Batch 53 - Data loading...
[Train & Eval] Val Batch 54 - Data loading...
[Train & Eval] Val Batch 55 - Data loading...
[Train & Eval] Val Batch 56 - Data loading...
[Train & Eval] Val Batch 57 - Data loading...
[Train & Eval] Val Batch 58 - Data loading...
[Train & Eval] Val Batch 59 - Data loading...
[Train & Eval] Val Batch 60 - Data loading...
[Train & Eval] Val Batch 61 - Data loading...
[Train & Eval] Val Batch 62 - Data loading...
[Train & Eval] Val Batch 63 - Data

[Train & Eval] Val Batch 215 - Data loading...
[Train & Eval] Val Batch 216 - Data loading...
[Train & Eval] Val Batch 217 - Data loading...
[Train & Eval] Val Batch 218 - Data loading...
[Train & Eval] Val Batch 219 - Data loading...
[Train & Eval] Val Batch 220 - Data loading...
[Train & Eval] Val Batch 221 - Data loading...
[Train & Eval] Val Batch 222 - Data loading...
[Train & Eval] Val Batch 223 - Data loading...
[Train & Eval] Val Batch 224 - Data loading...
[Train & Eval] Val Batch 225 - Data loading...
[Train & Eval] Val Batch 226 - Data loading...
[Train & Eval] Val Batch 227 - Data loading...
[Train & Eval] Val Batch 228 - Data loading...
[Train & Eval] Val Batch 229 - Data loading...
[Train & Eval] Val Batch 230 - Data loading...
[Train & Eval] Val Batch 231 - Data loading...
[Train & Eval] Val Batch 232 - Data loading...
[Train & Eval] Val Batch 233 - Data loading...
[Train & Eval] Val Batch 234 - Data loading...
[Train & Eval] Val Batch 235 - Data loading...
[Train & Eval

[Train & Eval] Val Batch 386 - Data loading...
[Train & Eval] Val Batch 387 - Data loading...
[Train & Eval] Val Batch 388 - Data loading...
[Train & Eval] Val Batch 389 - Data loading...
[Train & Eval] Val Batch 390 - Data loading...
[Train & Eval] Val Batch 391 - Data loading...
[Train & Eval] Val Batch 392 - Data loading...
[Train & Eval] Val Batch 393 - Data loading...
[Train & Eval] Val Batch 394 - Data loading...
[Train & Eval] Val Batch 395 - Data loading...
[Train & Eval] Val Batch 396 - Data loading...
[Train & Eval] Val Batch 397 - Data loading...
[Train & Eval] Val Batch 398 - Data loading...
[Train & Eval] Val Batch 399 - Data loading...
[Train & Eval] Val Batch 400 - Data loading...
[Train & Eval] Val Batch 401 - Data loading...
[Train & Eval] Val Batch 402 - Data loading...
[Train & Eval] Val Batch 403 - Data loading...
[Train & Eval] Val Batch 404 - Data loading...
[Train & Eval] Val Batch 405 - Data loading...
[Train & Eval] Val Batch 406 - Data loading...
[Train & Eval

[Train & Eval] Val Batch 557 - Data loading...
[Train & Eval] Val Batch 558 - Data loading...
[Train & Eval] Val Batch 559 - Data loading...
[Train & Eval] Val Batch 560 - Data loading...
[Train & Eval] Val Batch 561 - Data loading...
[Train & Eval] Val Batch 562 - Data loading...
[Train & Eval] Val Batch 563 - Data loading...
[Train & Eval] Val Batch 564 - Data loading...
[Train & Eval] Val Batch 565 - Data loading...
[Train & Eval] Val Batch 566 - Data loading...
[Train & Eval] Val Batch 567 - Data loading...
[Train & Eval] Val Batch 568 - Data loading...
[Train & Eval] Val Batch 569 - Data loading...
[Train & Eval] Val Batch 570 - Data loading...
[Train & Eval] Val Batch 571 - Data loading...
[Train & Eval] Val Batch 572 - Data loading...
[Train & Eval] Val Batch 573 - Data loading...
[Train & Eval] Val Batch 574 - Data loading...
[Step 5] Epoch 5/5 | Train Loss: 0.1524 | Val Acc: 93.71%
[Step 6] Model ResNet50 achieved validation accuracy: 93.71%

=== Step 6: Model Selection Result

In [2]:
# Define the filename
model_save_path = "best_model_v1.pth"

# Save the model's state dictionary
torch.save(candidates[best_model_name].state_dict(), model_save_path)

print(f"[Step 7] Model saved successfully as {model_save_path} in the current directory.")


[Step 7] Model saved successfully as best_model_v1.pth in the current directory.


In [3]:
#Advance Model

In [ ]:
import os
import pandas as pd
from PIL import Image
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader, random_split
from torchvision import transforms, models

# ======================================================
# Device Setup: Use MPS (M1/M2 Mac), CUDA, or CPU
# ======================================================
if torch.backends.mps.is_available():
    device = torch.device("mps")
elif torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")
print(f"[Device Setup] Using device: {device}\n")

# ======================================================
# Load CSV and Validate Data
# ======================================================
base_dir = '/Users/bhaskarpramodchennupalli/Documents/Image_Detector'
csv_path = os.path.join(base_dir, 'train.csv')
train_data_dir = os.path.join(base_dir, 'train_data')

print("=== Step 1: Data Validation ===")
df = pd.read_csv(csv_path).drop(columns=['Unnamed: 0'], errors='ignore')
print(f"[Step 1] Loaded {len(df)} records from CSV.")

# Check if all images exist
missing_files = [os.path.join(train_data_dir, os.path.basename(f)) for f in df['file_name'] if not os.path.exists(os.path.join(train_data_dir, os.path.basename(f)))]
if missing_files:
    print(f"[Step 1] Warning: {len(missing_files)} files missing!")
    for f in missing_files[:5]: print(f"    Missing: {f}")
else:
    print("[Step 1] All files exist.\n")

# ======================================================
# Custom Dataset Class
# ======================================================
print("=== Step 2: Dataset Class ===")
class CustomImageDataset(Dataset):
    def __init__(self, csv_file, transform=None):
        self.data_frame = pd.read_csv(csv_file).drop(columns=['Unnamed: 0'], errors='ignore')
        self.transform = transform
        print(f"[Dataset] Loaded {len(self.data_frame)} records.")

    def __len__(self):
        return len(self.data_frame)

    def __getitem__(self, idx):
        file_path = self.data_frame.iloc[idx]['file_name']
        full_path = os.path.join(train_data_dir, os.path.basename(file_path))
        try:
            image = Image.open(full_path).convert("RGB")
        except Exception as e:
            print(f"[Dataset] Error loading image: {full_path}, error: {e}")
            image = Image.new("RGB", (224, 224), "white")
        
        if self.transform:
            image = self.transform(image)
        label = self.data_frame.iloc[idx]['label']
        return image, torch.tensor(label, dtype=torch.float32).unsqueeze(0)

print("[Step 2] Dataset class defined.\n")

# ======================================================
# Model Selection: ResNet, EfficientNet, DenseNet, ViT
# ======================================================
print("=== Step 3: Model Selection ===")

def create_model(model_type="resnet50"):
    print(f"[Model] Initializing {model_type}...")
    if model_type == "resnet50":
        model = models.resnet50(weights=models.ResNet50_Weights.DEFAULT)
    elif model_type == "resnet101":
        model = models.resnet101(weights=models.ResNet101_Weights.DEFAULT)
    elif model_type == "resnet152":
        model = models.resnet152(weights=models.ResNet152_Weights.DEFAULT)
    elif model_type == "efficientnet":
        model = models.efficientnet_b0(weights=models.EfficientNet_B0_Weights.DEFAULT)
        model.classifier[1] = nn.Linear(model.classifier[1].in_features, 1)
    elif model_type == "densenet":
        model = models.densenet121(weights=models.DenseNet121_Weights.DEFAULT)
        model.classifier = nn.Linear(model.classifier.in_features, 1)
    elif model_type == "vit":
        model = models.vit_b_16(weights=models.ViT_B_16_Weights.DEFAULT)
        model.heads.head = nn.Linear(model.heads.head.in_features, 1)
    else:
        raise ValueError(f"[Model] Error: {model_type} is not supported!")

    # Modify last layer for binary classification
    if "resnet" in model_type:
        model.fc = nn.Linear(model.fc.in_features, 1)

    return model.to(device)

# Model Dictionary
model_types = ["resnet50", "resnet101", "resnet152", "efficientnet", "densenet", "vit"]
models_dict = {name: create_model(name) for name in model_types}
print("[Step 3] Models initialized.\n")

# ======================================================
# Training Function
# ======================================================
print("=== Step 4: Training ===")
def train_and_evaluate(model, train_loader, val_loader, num_epochs=5):
    criterion = nn.BCEWithLogitsLoss()
    optimizer = optim.Adam(model.parameters(), lr=0.001)
    model.to(device)
    
    best_val_acc = 0.0
    print("[Training] Starting training...")
    for epoch in range(num_epochs):
        print(f"\n[Epoch {epoch+1}/{num_epochs}]")
        
        # Training Phase
        model.train()
        running_loss = 0.0
        for batch_idx, (images, labels) in enumerate(train_loader):
            images, labels = images.to(device), labels.to(device)
            optimizer.zero_grad()
            outputs = model(images)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()
            running_loss += loss.item() * images.size(0)
            if batch_idx % 50 == 0:
                print(f"[Batch {batch_idx}] Loss: {loss.item():.4f}")

        avg_loss = running_loss / len(train_loader.dataset)

        # Validation Phase
        model.eval()
        correct, total = 0, 0
        with torch.no_grad():
            for images, labels in val_loader:
                images, labels = images.to(device), labels.to(device)
                outputs = model(images)
                preds = torch.round(torch.sigmoid(outputs))
                total += labels.size(0)
                correct += (preds == labels).sum().item()

        val_acc = correct / total
        best_val_acc = max(best_val_acc, val_acc)
        print(f"[Epoch {epoch+1}] Train Loss: {avg_loss:.4f} | Val Acc: {val_acc*100:.2f}%")

    return best_val_acc

# ======================================================
# Main Execution Block (Fix multiprocessing issue)
# ======================================================
if __name__ == "__main__":
    print("=== Step 5: Data Preparation ===")
    transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor(),
    ])
    full_dataset = CustomImageDataset(csv_file=csv_path, transform=transform)

    train_size = int(0.8 * len(full_dataset))
    val_size = len(full_dataset) - train_size
    train_dataset, val_dataset = random_split(full_dataset, [train_size, val_size])

    batch_size = 32
    num_workers = 8  # Use 8 workers for faster data loading
    train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=num_workers, pin_memory=True)
    val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False, num_workers=num_workers, pin_memory=True)
    print("[Step 5] DataLoaders ready.")

    # Train models
    num_epochs = 5
    results = {}

    for model_name, model_instance in models_dict.items():
        print(f"\n=== Training {model_name.upper()} ===")
        val_acc = train_and_evaluate(model_instance, train_loader, val_loader, num_epochs)
        results[model_name] = val_acc
        print(f"[Result] {model_name} -> Val Acc: {val_acc*100:.2f}%\n")

    best_model = max(results, key=results.get)
    print(f"🏆 Best Model: {best_model} with {results[best_model]*100:.2f}% validation accuracy.")


[Device Setup] Using device: mps

=== Step 1: Data Validation ===
[Step 1] Loaded 91950 records from CSV.
[Step 1] All files exist.

=== Step 2: Dataset Class ===
[Step 2] Dataset class defined.

=== Step 3: Model Selection ===
[Model] Initializing resnet50...
[Model] Initializing resnet101...
[Model] Initializing resnet152...
[Model] Initializing efficientnet...
[Model] Initializing densenet...
[Model] Initializing vit...
[Step 3] Models initialized.

=== Step 4: Training ===
=== Step 5: Data Preparation ===
[Dataset] Loaded 91950 records.
[Step 5] DataLoaders ready.

=== Training RESNET50 ===
[Training] Starting training...

[Epoch 1/5]


Traceback (most recent call last):
  File "<string>", line 1, in <module>
  File "/Users/bhaskarpramodchennupalli/anaconda3/lib/python3.11/multiprocessing/spawn.py", line 122, in spawn_main
    exitcode = _main(fd, parent_sentinel)
               ^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/Users/bhaskarpramodchennupalli/anaconda3/lib/python3.11/multiprocessing/spawn.py", line 132, in _main
    self = reduction.pickle.load(from_parent)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
AttributeError: Can't get attribute 'CustomImageDataset' on <module '__main__' (built-in)>
